# Loop for extract points 

In [1]:
import geopandas as gpd
from shapely.geometry import LineString, Point
import geopandas as gpd
import rasterio
from rasterio.transform import from_origin
from rasterio.enums import Resampling
from shapely.geometry import Point
import numpy as np
import pandas as pd
import pandas as pd


## Create Transect/Perpendiculars Smooth Line

In [2]:
import geopandas as gpd
from shapely.geometry import LineString

In [3]:
df_point = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\mod_el.shp")

In [4]:
# Smooth short stream
# df = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\01-Multiple_transects\new_branch_small_smooth_split.shp")

df = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\03-Shapefile\01-New_domain_data\10-Operations\01-DEM_burn\03-longBranch\Transacts\new_longbranch_se_SmoothLine.shp")

#### Split lines in equal intervals

In [5]:
# df = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\03-Shapefile\01-New_domain_data\10-Operations\01-DEM_burn\03-longBranch\Transacts\new_longbranch_se_SmoothLine.shp")

In [6]:
df = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\01-Multiple_transects\LongBranch_smooth_dissolved.shp")

In [7]:
df

Shape_Leng                                           geometry
0  5842.700441  LINESTRING (302421.000 4300250.000, 302421.897...

In [8]:
original_line = df.loc[0, 'geometry']

segment_length = 2.0
# Calculate the total length of the line
total_length = original_line.length
num_segments = int(total_length / segment_length)

# Calculate the length of each segment
segment_length_actual = total_length / num_segments

# Create a list to store the segment geometries
segments = []

# Iterate through each segment and create LineString segments
for i in range(num_segments):
    start_distance = i * segment_length_actual
    end_distance = (i + 1) * segment_length_actual

    # Create a LineString segment using the two points as coordinates
    segment = LineString(
        [original_line.interpolate(start_distance), original_line.interpolate(end_distance)]
    )

    # Assign a unique ID to each segment
    segment_id = i + 1  # You can adjust the starting ID as needed

    # Create a dictionary to store the segment along with its ID
    segment_with_id = {'id': segment_id, 'geometry': segment}

    # Append the segment to the list
    segments.append(segment_with_id)

# Convert the list of segments to a GeoDataFrame
segments_gdf = gpd.GeoDataFrame(segments, geometry='geometry')

# Now 'segments_gdf' is a GeoDataFrame containing LineString segments with unique IDs


In [9]:
segments_gdf

id                                           geometry
0        1  LINESTRING (302421.000 4300250.000, 302422.408...
1        2  LINESTRING (302422.408 4300248.580, 302423.737...
2        3  LINESTRING (302423.737 4300247.086, 302424.834...
3        4  LINESTRING (302424.834 4300245.417, 302426.000...
4        5  LINESTRING (302426.000 4300243.792, 302427.136...
...    ...                                                ...
2916  2917  LINESTRING (305950.480 4298126.691, 305952.384...
2917  2918  LINESTRING (305952.384 4298126.084, 305954.068...
2918  2919  LINESTRING (305954.068 4298125.012, 305955.585...
2919  2920  LINESTRING (305955.585 4298123.721, 305956.963...
2920  2921  LINESTRING (305956.963 4298122.272, 305958.500...

[2921 rows x 2 columns]

In [424]:
output_path = r'C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\first_transact_line12345678917.shp'
segments_gdf.to_file(output_path, driver='ESRI Shapefile')

### Create Perpendiculars along line

In [10]:
from shapely.geometry import LineString, MultiPoint
import geopandas as gpd
import numpy as np


In [11]:
df = segments_gdf

In [12]:
# midpoint - works

def generate_perpendicular_lines(linestring):
    vertices = list(linestring.coords)
    perp_lines = []
    
    for i in range(len(vertices)-1):
        start_point = vertices[i]
        end_point = vertices[i+1]
        
        # Calculate the midpoint of the original line segment
        midpoint = MultiPoint([start_point, end_point]).centroid
        
        # Calculate the angle of the original line segment
        angle = np.arctan2(end_point[1] - start_point[1], end_point[0] - start_point[0])
        
        # Add 90 degrees to get the perpendicular direction
        angle_perpendicular = angle + np.pi/2
        
        # Calculate the half-length of the perpendicular line
        half_length = 20  # Adjust this value based on your requirements
        
        # Calculate the endpoints of the perpendicular line
        endpoint1 = (
            midpoint.x + np.cos(angle_perpendicular) * half_length,
            midpoint.y + np.sin(angle_perpendicular) * half_length
        )
        
        endpoint2 = (
            midpoint.x - np.cos(angle_perpendicular) * half_length,
            midpoint.y - np.sin(angle_perpendicular) * half_length
        )
        
        perp_lines.append(LineString([endpoint1, endpoint2]))
    
    return perp_lines

# Assuming df is your original GeoDataFrame with polyline geometries
df['perp_lines'] = df.apply(lambda x: generate_perpendicular_lines(linestring=x.geometry), axis=1)

# Create a new GeoDataFrame
df2 = gpd.GeoDataFrame(geometry=df['perp_lines'].explode().reset_index(drop=True), crs="EPSG:26918")

# Save to a Shapefile
df2.to_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\\perpendicular_lines102.shp")


## For 1 Transect

### Transect Load:

In [260]:
gdf_line = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\03-Shapefile\01-New_domain_data\10-Operations\01-DEM_burn\04-Transacts\2_transect_line.shp")

### Create Points along the Transect

In [261]:
line = gdf_line['geometry'].iloc[0] 

distance = 0  
add_distance = 1  

list_of_points = []

while distance < line.length:
    new_point = line.interpolate(distance)
    list_of_points.append(new_point)
    distance += add_distance

# GeoDataFrame with multipoints
gdf_multipoints = gpd.GeoDataFrame(geometry=gpd.GeoSeries(list_of_points))

#### Transect_ID

In [262]:
gdf_multipoints['point_id'] = range(1, len(gdf_multipoints) + 1)

#### set Projection

In [263]:
gdf_multipoints = gdf_multipoints.set_crs(gdf_line.crs)

In [264]:
gdf_multipoints

geometry  point_id
0   POINT (304626.634 4298977.520)         1
1   POINT (304627.139 4298976.657)         2
2   POINT (304627.644 4298975.793)         3
3   POINT (304628.148 4298974.930)         4
4   POINT (304628.653 4298974.067)         5
5   POINT (304629.158 4298973.204)         6
6   POINT (304629.663 4298972.341)         7
7   POINT (304630.168 4298971.477)         8
8   POINT (304630.673 4298970.614)         9
9   POINT (304631.178 4298969.751)        10
10  POINT (304631.683 4298968.888)        11
11  POINT (304632.188 4298968.025)        12
12  POINT (304632.692 4298967.161)        13
13  POINT (304633.197 4298966.298)        14
14  POINT (304633.702 4298965.435)        15
15  POINT (304634.207 4298964.572)        16
16  POINT (304634.712 4298963.709)        17
17  POINT (304635.217 4298962.846)        18
18  POINT (304635.722 4298961.982)        19
19  POINT (304636.227 4298961.119)        20
20  POINT (304636.731 4298960.256)        21
21  POINT (304637.236 4298959.393)        22
22  POINT (304637.741 4298958.530)        23
23  POINT (304638.246 4298957.666)        24
24  POINT (304638.751 4298956.803)        25
25  POINT (304639.256 4298955.940)        26
26  POINT (304639.761 4298955.077)        27
27  POINT (304640.266 4298954.214)        28
28  POINT (304640.771 4298953.350)        29
29  POINT (304641.275 4298952.487)        30
30  POINT (304641.780 4298951.624)        31
31  POINT (304642.285 4298950.761)        32
32  POINT (304642.790 4298949.898)        33
33  POINT (304643.295 4298949.034)        34
34  POINT (304643.800 4298948.171)        35
35  POINT (304644.305 4298947.308)        36
36  POINT (304644.810 4298946.445)        37
37  POINT (304645.314 4298945.582)        38
38  POINT (304645.819 4298944.719)        39
39  POINT (304646.324 4298943.855)        40
40  POINT (304646.829 4298942.992)        41
41  POINT (304647.334 4298942.129)        42
42  POINT (304647.839 4298941.266)        43
43  POINT (304648.344 4298940.403)        44
44  POINT (304648.849 4298939.539)        45
45  POINT (304649.354 4298938.676)        46
46  POINT (304649.858 4298937.813)        47
47  POINT (304650.363 4298936.950)        48
48  POINT (304650.868 4298936.087)        49
49  POINT (304651.373 4298935.223)        50
50  POINT (304651.878 4298934.360)        51

### Sample Values

In [265]:
def extract_raster_values(point, src):
    values = list(src.sample([(point.x, point.y)]))

    # Return the sampled values as float
    return float(values[0][0]) if values and not np.isnan(values[0][0]) else np.nan


In [266]:
df_points = gdf_multipoints  
raster_path = r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\03-Shapefile\01-New_domain_data\02-DEM\02-Fairfax_County_2018\clip\clip_ffxco.tif"
src = rasterio.open(raster_path)
df_points['raster_values'] = round(df_points['geometry'].apply(lambda geom: extract_raster_values(geom, src)), 4)
src.close()

C:\Users\zkhalid5\AppData\Roaming\Python\Python311\site-packages\geopandas\geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)


In [267]:
df_points

geometry  point_id  raster_values
0   POINT (304626.634 4298977.520)         1        74.3115
1   POINT (304627.139 4298976.657)         2        74.3577
2   POINT (304627.644 4298975.793)         3        74.3182
3   POINT (304628.148 4298974.930)         4        74.2613
4   POINT (304628.653 4298974.067)         5        74.2613
5   POINT (304629.158 4298973.204)         6        74.2985
6   POINT (304629.663 4298972.341)         7        74.3050
7   POINT (304630.168 4298971.477)         8        74.3730
8   POINT (304630.673 4298970.614)         9        74.4282
9   POINT (304631.178 4298969.751)        10        74.4147
10  POINT (304631.683 4298968.888)        11        74.4160
11  POINT (304632.188 4298968.025)        12        74.3933
12  POINT (304632.692 4298967.161)        13        74.3648
13  POINT (304633.197 4298966.298)        14        74.3392
14  POINT (304633.702 4298965.435)        15        74.3692
15  POINT (304634.207 4298964.572)        16        74.3487
16  POINT (304634.712 4298963.709)        17        74.3353
17  POINT (304635.217 4298962.846)        18        74.3078
18  POINT (304635.722 4298961.982)        19        74.2910
19  POINT (304636.227 4298961.119)        20        74.3058
20  POINT (304636.731 4298960.256)        21        74.3304
21  POINT (304637.236 4298959.393)        22        74.2693
22  POINT (304637.741 4298958.530)        23        74.1202
23  POINT (304638.246 4298957.666)        24        73.4930
24  POINT (304638.751 4298956.803)        25        73.2998
25  POINT (304639.256 4298955.940)        26        73.2947
26  POINT (304639.761 4298955.077)        27        73.2947
27  POINT (304640.266 4298954.214)        28        73.3717
28  POINT (304640.771 4298953.350)        29        73.3955
29  POINT (304641.275 4298952.487)        30        73.4934
30  POINT (304641.780 4298951.624)        31        73.5064
31  POINT (304642.285 4298950.761)        32        73.6972
32  POINT (304642.790 4298949.898)        33        73.8793
33  POINT (304643.295 4298949.034)        34        73.9938
34  POINT (304643.800 4298948.171)        35        74.1278
35  POINT (304644.305 4298947.308)        36        74.2731
36  POINT (304644.810 4298946.445)        37        74.2712
37  POINT (304645.314 4298945.582)        38        74.2766
38  POINT (304645.819 4298944.719)        39        74.3453
39  POINT (304646.324 4298943.855)        40        74.4469
40  POINT (304646.829 4298942.992)        41        74.4065
41  POINT (304647.334 4298942.129)        42        74.4215
42  POINT (304647.839 4298941.266)        43        74.3738
43  POINT (304648.344 4298940.403)        44        74.3436
44  POINT (304648.849 4298939.539)        45        74.3607
45  POINT (304649.354 4298938.676)        46        74.3731
46  POINT (304649.858 4298937.813)        47        74.3848
47  POINT (304650.363 4298936.950)        48        74.3064
48  POINT (304650.868 4298936.087)        49        74.3064
49  POINT (304651.373 4298935.223)        50        74.2082
50  POINT (304651.878 4298934.360)        51        74.1812

### Calculate Slope

In [21]:
def calculate_relative_slope (df_point):
    """
    Function calculates the slope by finding the minimum elevation point ('RASTERVALU') and 
    then calculates the slope on both sides of this minimum point. It creates two separate
    DataFrames (left_df and right_df) for points on the left and right sides of the minimum
    point. The slope is calculated by dividing the difference in elevation by the difference
    in index values. Finally, it concatenates these DataFrames to get the final result.
    """
    # Base point i.e. min 'RASTERVALU'
    min_index = df_point['raster_values'].idxmin()
    base_point = df_point.loc[min_index]

    # separate left from base and calculate slope
    left_df = df_point.loc[:min_index].copy()
    left_df['slope'] = (base_point['raster_values'] - left_df['raster_values']) / left_df['point_id'].diff()

    # do same for right side
    right_df = df_point.loc[min_index:].copy()
    right_df['slope'] = (right_df['raster_values'].shift(-1) - base_point['raster_values']) / right_df['point_id'].diff()

    # Concatenate both
    df_point['slope'] = pd.concat([left_df['slope'], right_df['slope'].iloc[1:]])

    # optional
    # df_point['slope'] = df_point['slope'].fillna(-999)
    
    return df_point

In [269]:
df_points = calculate_relative_slope (df_points)

In [270]:
df_points

geometry  point_id  raster_values     slope
0   POINT (304626.634 4298977.520)         1        74.3115 -999.0000
1   POINT (304627.139 4298976.657)         2        74.3577   -1.0630
2   POINT (304627.644 4298975.793)         3        74.3182   -1.0235
3   POINT (304628.148 4298974.930)         4        74.2613   -0.9666
4   POINT (304628.653 4298974.067)         5        74.2613   -0.9666
5   POINT (304629.158 4298973.204)         6        74.2985   -1.0038
6   POINT (304629.663 4298972.341)         7        74.3050   -1.0103
7   POINT (304630.168 4298971.477)         8        74.3730   -1.0783
8   POINT (304630.673 4298970.614)         9        74.4282   -1.1335
9   POINT (304631.178 4298969.751)        10        74.4147   -1.1200
10  POINT (304631.683 4298968.888)        11        74.4160   -1.1213
11  POINT (304632.188 4298968.025)        12        74.3933   -1.0986
12  POINT (304632.692 4298967.161)        13        74.3648   -1.0701
13  POINT (304633.197 4298966.298)        14        74.3392   -1.0445
14  POINT (304633.702 4298965.435)        15        74.3692   -1.0745
15  POINT (304634.207 4298964.572)        16        74.3487   -1.0540
16  POINT (304634.712 4298963.709)        17        74.3353   -1.0406
17  POINT (304635.217 4298962.846)        18        74.3078   -1.0131
18  POINT (304635.722 4298961.982)        19        74.2910   -0.9963
19  POINT (304636.227 4298961.119)        20        74.3058   -1.0111
20  POINT (304636.731 4298960.256)        21        74.3304   -1.0357
21  POINT (304637.236 4298959.393)        22        74.2693   -0.9746
22  POINT (304637.741 4298958.530)        23        74.1202   -0.8255
23  POINT (304638.246 4298957.666)        24        73.4930   -0.1983
24  POINT (304638.751 4298956.803)        25        73.2998   -0.0051
25  POINT (304639.256 4298955.940)        26        73.2947    0.0000
26  POINT (304639.761 4298955.077)        27        73.2947    0.0770
27  POINT (304640.266 4298954.214)        28        73.3717    0.1008
28  POINT (304640.771 4298953.350)        29        73.3955    0.1987
29  POINT (304641.275 4298952.487)        30        73.4934    0.2117
30  POINT (304641.780 4298951.624)        31        73.5064    0.4025
31  POINT (304642.285 4298950.761)        32        73.6972    0.5846
32  POINT (304642.790 4298949.898)        33        73.8793    0.6991
33  POINT (304643.295 4298949.034)        34        73.9938    0.8331
34  POINT (304643.800 4298948.171)        35        74.1278    0.9784
35  POINT (304644.305 4298947.308)        36        74.2731    0.9765
36  POINT (304644.810 4298946.445)        37        74.2712    0.9819
37  POINT (304645.314 4298945.582)        38        74.2766    1.0506
38  POINT (304645.819 4298944.719)        39        74.3453    1.1522
39  POINT (304646.324 4298943.855)        40        74.4469    1.1118
40  POINT (304646.829 4298942.992)        41        74.4065    1.1268
41  POINT (304647.334 4298942.129)        42        74.4215    1.0791
42  POINT (304647.839 4298941.266)        43        74.3738    1.0489
43  POINT (304648.344 4298940.403)        44        74.3436    1.0660
44  POINT (304648.849 4298939.539)        45        74.3607    1.0784
45  POINT (304649.354 4298938.676)        46        74.3731    1.0901
46  POINT (304649.858 4298937.813)        47        74.3848    1.0117
47  POINT (304650.363 4298936.950)        48        74.3064    1.0117
48  POINT (304650.868 4298936.087)        49        74.3064    0.9135
49  POINT (304651.373 4298935.223)        50        74.2082    0.8865
50  POINT (304651.878 4298934.360)        51        74.1812 -999.0000

### Filtering Streams

In [271]:
# def filter_slope_range(df_point):
#     """
#     Function calculates the slope by finding the minimum elevation point ('RASTERVALU') and 
#     then calculates the slope on both sides of this minimum point. It creates two separate
#     DataFrames (left_df and right_df) for points on the left and right sides of the minimum
#     point. The slope is calculated by dividing the difference in elevation by the difference
#     in index values. Finally, it concatenates these DataFrames, filters out rows with slopes
#     not in the range (-1, 1), and returns the final result.
#     """
#     # Base point i.e., min 'RASTERVALU'
#     min_index = df_point['raster_values'].idxmin()
#     base_point = df_point.loc[min_index]

#     # Separate left from base and calculate slope
#     left_df = df_point.loc[:min_index].copy()
#     left_df['slope'] = (base_point['raster_values'] - left_df['raster_values']) / left_df['point_id'].diff()

#     # Do the same for the right side
#     right_df = df_point.loc[min_index:].copy()
#     right_df['slope'] = (right_df['raster_values'].shift(-1) - base_point['raster_values']) / right_df['point_id'].diff()

#     # Concatenate both
#     df_point['slope'] = pd.concat([left_df['slope'], right_df['slope'].iloc[1:]])

#     # Filter rows with slopes in the range (-1, 1) and consistent transect_id difference
#     filtered_df = df_point[
#         (df_point['slope'] >= -0.481299) & 
#         (df_point['slope'] <= 0.870400) &
#         (df_point['point_id'].diff().eq(df_point['point_id'].diff().iloc[1]))
#     ]

 
#     # Optional: Reset index
#     filtered_df = filtered_df.reset_index(drop=True)

#     return filtered_df


# def prune_middle_to_bottom(df):
#     '''
#     start from middle and move downward checking transect_id difference of each row 
#     if difference is greater than 2 then delete all the rows above it
#     '''
#     middle_index = len(df) // 2
#     for i in range(middle_index, len(df)-1):
#         current_id = df.loc[i, 'point_id']
#         next_id = df.loc[i+1, 'point_id']
#         if abs(current_id - next_id) > 2:
#             if i < middle_index:
#                 df = df[i+1:]
#             else:
#                 df = df[:i+1]
#             break  
#     return df

# def prune_bottom_to_top (df):
#     '''
#     start from bottom and move upward checking transect_id difference of each row 
#     if difference is greater than 2 then delete all the rows above it
#     '''
#     for i in range(len(df)-1, 0, -1):
#         current_id = df.loc[i, 'point_id']
#         prev_id = df.loc[i-1, 'point_id']
#         if abs(current_id - prev_id) > 2:            
#             df = df[i:]
#             break
#     return df

# filtered_df = filter_slope_range(df_points)
# filtered_df = prune_middle_to_bottom(filtered_df)
# filtered_df = prune_bottom_to_top(filtered_df)

In [22]:
def filter_slope_range(df_point):
    """
    Function calculates the slope by finding the minimum elevation point ('RASTERVALU') and 
    then calculates the slope on both sides of this minimum point. It creates two separate
    DataFrames (left_df and right_df) for points on the left and right sides of the minimum
    point. The slope is calculated by dividing the difference in elevation by the difference
    in index values. Finally, it concatenates these DataFrames, filters out rows with slopes
    not in the range (-1, 1), and returns the final result.
    """
    # Base point i.e., min 'RASTERVALU'
    min_index = df_point['raster_values'].idxmin()
    base_point = df_point.loc[min_index]

    # Separate left from base and calculate slope
    left_df = df_point.loc[:min_index].copy()
    left_df['slope'] = (base_point['raster_values'] - left_df['raster_values']) / left_df['point_id'].diff()

    # Do the same for the right side
    right_df = df_point.loc[min_index:].copy()
    right_df['slope'] = (right_df['raster_values'].shift(-1) - base_point['raster_values']) / right_df['point_id'].diff()

    # Concatenate both
    df_point['slope'] = pd.concat([left_df['slope'], right_df['slope'].iloc[1:]])
    
    
    # Drop rows where slope is NaN
    df_point = df_point.dropna(subset=['slope'])

    
    # Filter rows with slopes in the range (-1, 1) and consistent transect_id difference
    filtered_df = df_point[
        (df_point['slope'] >= -0.481299) & 
        (df_point['slope'] <= 0.870400) &
        (df_point['point_id'].diff().eq(df_point['point_id'].diff().iloc[1]))
    ]

 
    # Optional: Reset index
    filtered_df = filtered_df.reset_index(drop=True)

    return filtered_df


def prune_middle_to_bottom(df):
    '''
    start from middle and move downward checking transect_id difference of each row 
    if difference is greater than 2 then delete all the rows above it
    '''
    middle_index = len(df) // 2
    for i in range(middle_index, len(df)-1):
        current_id = df.loc[i, 'point_id']
        next_id = df.loc[i+1, 'point_id']
        if abs(current_id - next_id) > 2:
            if i < middle_index:
                df = df[i+1:]
            else:
                df = df[:i+1]
            break  
    return df

def prune_bottom_to_top (df):
    '''
    start from bottom and move upward checking transect_id difference of each row 
    if difference is greater than 2 then delete all the rows above it
    '''
    for i in range(len(df)-1, 0, -1):
        current_id = df.loc[i, 'point_id']
        prev_id = df.loc[i-1, 'point_id']
        if abs(current_id - prev_id) > 2:            
            df = df[i:]
            break
    return df

filtered_df = filter_slope_range(df_points)
filtered_df = prune_middle_to_bottom(filtered_df)
filtered_df = prune_bottom_to_top(filtered_df)

NameError: name 'df_points' is not defined

In [274]:
# def prune_middle_to_bottom(df):
#     '''
#     start from middle and move downward checking transect_id difference of each row 
#     if difference is greater than 2 then delete all the rows above it
#     '''
#     middle_index = len(df) // 2
#     for i in range(middle_index, len(df)-1):
#         current_id = df.loc[i, 'point_id']
#         next_id = df.loc[i+1, 'point_id']
#         if abs(current_id - next_id) > 2:
#             if i < middle_index:
#                 df = df[i+1:]
#             else:
#                 df = df[:i+1]
#             break  
#     return df

                          geometry  transect_id  raster_values   slope
0   POINT (304628.148 4298974.930)            4        74.2613 -0.9666
1   POINT (304628.653 4298974.067)            5        74.2613 -0.9666
2   POINT (304635.722 4298961.982)           19        74.2910 -0.9963
3   POINT (304637.236 4298959.393)           22        74.2693 -0.9746
4   POINT (304637.741 4298958.530)           23        74.1202 -0.8255
5   POINT (304638.246 4298957.666)           24        73.4930 -0.1983
6   POINT (304638.751 4298956.803)           25        73.2998 -0.0051
7   POINT (304639.256 4298955.940)           26        73.2947  0.0000
8   POINT (304639.761 4298955.077)           27        73.2947  0.0770
9   POINT (304640.266 4298954.214)           28        73.3717  0.1008
10  POINT (304640.771 4298953.350)           29        73.3955  0.1987
11  POINT (304641.275 4298952.487)           30        73.4934  0.2117
12  POINT (304641.780 4298951.624)           31        73.5064  0.4025
13  PO

In [275]:
# def prune_bottom_to_top (df):
#     '''
#     start from bottom and move upward checking transect_id difference of each row 
#     if difference is greater than 2 then delete all the rows above it
#     '''
#     for i in range(len(df)-1, 0, -1):
#         current_id = df.loc[i, 'point_id']
#         prev_id = df.loc[i-1, 'point_id']
#         if abs(current_id - prev_id) > 2:            
#             df = df[i:]
#             break
#     return df


In [276]:
filtered_df = filter_slope_range(df_points)
filtered_df = prune_middle_to_bottom(filtered_df)
filtered_df = prune_bottom_to_top(filtered_df)

In [277]:
filtered_df

geometry  point_id  raster_values   slope
3   POINT (304637.236 4298959.393)        22        74.2693 -0.9746
4   POINT (304637.741 4298958.530)        23        74.1202 -0.8255
5   POINT (304638.246 4298957.666)        24        73.4930 -0.1983
6   POINT (304638.751 4298956.803)        25        73.2998 -0.0051
7   POINT (304639.256 4298955.940)        26        73.2947  0.0000
8   POINT (304639.761 4298955.077)        27        73.2947  0.0770
9   POINT (304640.266 4298954.214)        28        73.3717  0.1008
10  POINT (304640.771 4298953.350)        29        73.3955  0.1987
11  POINT (304641.275 4298952.487)        30        73.4934  0.2117
12  POINT (304641.780 4298951.624)        31        73.5064  0.4025
13  POINT (304642.285 4298950.761)        32        73.6972  0.5846
14  POINT (304642.790 4298949.898)        33        73.8793  0.6991
15  POINT (304643.295 4298949.034)        34        73.9938  0.8331
16  POINT (304643.800 4298948.171)        35        74.1278  0.9784
17  POINT (304644.305 4298947.308)        36        74.2731  0.9765
18  POINT (304644.810 4298946.445)        37        74.2712  0.9819

### Bank Points


In [292]:

new_df = pd.DataFrame()

start_row = filtered_df.iloc[0]
end_row = filtered_df.iloc[-1]

for column in filtered_df.columns:
    new_df['start_' + column] = [start_row[column]]
    new_df['end_' + column] = [end_row[column]]


In [293]:
new_df

start_geometry  \
0  POINT (304637.23636673426 4298959.392750409)   

                                   end_geometry  start_point_id  end_point_id  \
0  POINT (304644.80961648107 4298946.444936375)              22            37   

   start_raster_values  end_raster_values  start_slope  end_slope  
0              74.2693            74.2712      -0.9746     0.9819

In [296]:
import geopandas as gpd
from shapely.geometry import Point
from shapely.wkt import dumps

# Assuming 'start_geometry' and 'end_geometry' are columns in your DataFrame
geometry = [Point(xy.x, xy.y) for xy in new_df['start_geometry']]
wkt_geometry = [dumps(point) for point in geometry]

# Create a GeoDataFrame from the DataFrame
geo_df = gpd.GeoDataFrame(new_df, geometry=gpd.GeoSeries(geometry))

# Save the GeoDataFrame to a shapefile
output_path = r'C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\first_transact_line12345678911.shp'
geo_df.to_file(output_path, driver='ESRI Shapefile')


C:\Users\zkhalid5\AppData\Local\Temp\ipykernel_2292\2876234146.py:14: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  geo_df.to_file(output_path, driver='ESRI Shapefile')


ValueError: Invalid field type <class 'shapely.geometry.point.Point'>

In [282]:
output_path = r'C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\first_transact_line12345678911.shp'
new_df.to_file(output_path, driver='ESRI Shapefile')

AttributeError: 'DataFrame' object has no attribute 'to_file'

## For Multiple Transects

### Multiple Transect File load

In [321]:
# gdf_line = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\01-Multiple_transects\Multiple_transects.shp")

# gdf_line = gpd.read_file(r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\01-Multiple_transects\Multiple_transects_sample.shp")

In [322]:
# gdf_line.crs

In [13]:
df2

geometry
0     LINESTRING (302435.909 4300263.369, 302407.499...
1     LINESTRING (302438.011 4300261.132, 302408.135...
2     LINESTRING (302441.001 4300257.233, 302407.571...
3     LINESTRING (302441.666 4300256.265, 302409.169...
4     LINESTRING (302443.019 4300254.344, 302410.117...
...                                                 ...
2916  LINESTRING (305957.507 4298145.442, 305945.357...
2917  LINESTRING (305963.964 4298142.421, 305942.489...
2918  LINESTRING (305967.791 4298139.595, 305941.862...
2919  LINESTRING (305970.762 4298136.784, 305941.786...
2920  LINESTRING (305970.486 4298137.042, 305944.978...

[2921 rows x 1 columns]

In [14]:
gdf_line = df2

In [15]:
line = gdf_line['geometry'].iloc[0] 

distance = 0  
add_distance = 1  

list_of_points = []

while distance < line.length:
    new_point = line.interpolate(distance)
    list_of_points.append(new_point)
    distance += add_distance

# GeoDataFrame with multipoints
gdf_multipoints = gpd.GeoDataFrame(geometry=gpd.GeoSeries(list_of_points))



#### Method 1

In [252]:
import geopandas as gpd
import pandas as pd

# Assuming gdf_line is your GeoDataFrame with LineString geometries

# Initialize an empty GeoDataFrame for storing multipoints
gdf_multipoints_all = gpd.GeoDataFrame()

for index, row in gdf_line.iterrows():
    line = row['geometry']  # Extract the LineString geometry from the current row

    distance = 0
    add_distance = 1
    list_of_points = []

    while distance < line.length:
        new_point = line.interpolate(distance)
        list_of_points.append(new_point)
        distance += add_distance

    # Create a GeoDataFrame for the current row
    gdf_multipoints_row = gpd.GeoDataFrame(geometry=gpd.GeoSeries(list_of_points))
    
    # Concatenate the current GeoDataFrame to the overall GeoDataFrame
    gdf_multipoints_all = pd.concat([gdf_multipoints_all, gdf_multipoints_row], ignore_index=True)

# gdf_multipoints_all now contains points along the lines of all rows in gdf_line


In [253]:
gdf_multipoints_all

geometry
0     POINT (304585.811 4298958.256)
1     POINT (304586.170 4298957.323)
2     POINT (304586.529 4298956.390)
3     POINT (304586.888 4298955.456)
4     POINT (304587.247 4298954.523)
...                              ...
1305  POINT (304601.986 4298916.268)
1306  POINT (304602.320 4298915.326)
1307  POINT (304602.654 4298914.383)
1308  POINT (304602.988 4298913.440)
1309  POINT (304603.321 4298912.498)

[1310 rows x 1 columns]

#### Method 2

In [254]:
import geopandas as gpd
from shapely.geometry import MultiPoint

# Assuming gdf_line is your GeoDataFrame with LineString geometries

# Initialize an empty list to store rows for the new GeoDataFrame
rows = []

for index, row in gdf_line.iterrows():
    line = row['geometry']  # Extract the LineString geometry from the current row

    distance = 0
    add_distance = 1
    list_of_points = []

    while distance < line.length:
        new_point = line.interpolate(distance)
        list_of_points.append(new_point)
        distance += add_distance

    # Append a row for the new GeoDataFrame
    rows.append({'geometry': MultiPoint(list_of_points), 'original_index': index})

# Create a new GeoDataFrame from the list of rows
gdf_multipoints_all = gpd.GeoDataFrame(rows, geometry='geometry')

# gdf_multipoints_all now contains points along the lines for each entry in gdf_line
# Each entry in gdf_multipoints_all is a MultiPoint geometry


In [255]:
gdf_multipoints_all

geometry  original_index
0   MULTIPOINT (304585.811 4298958.256, 304586.170...               0
1   MULTIPOINT (304586.368 4298958.449, 304586.684...               1
2   MULTIPOINT (304585.501 4298958.137, 304585.860...               2
3   MULTIPOINT (304586.460 4298958.478, 304586.756...               3
4   MULTIPOINT (304586.180 4298958.386, 304586.497...               4
5   MULTIPOINT (304585.215 4298958.080, 304585.537...               5
6   MULTIPOINT (304586.108 4298958.369, 304586.404...               6
7   MULTIPOINT (304585.025 4298958.015, 304585.349...               7
8   MULTIPOINT (304591.598 4298960.090, 304591.896...               8
9   MULTIPOINT (304588.647 4298958.989, 304589.050...               9
10  MULTIPOINT (304591.421 4298960.035, 304591.719...              10
11  MULTIPOINT (304588.431 4298958.894, 304588.834...              11
12  MULTIPOINT (304588.207 4298958.795, 304588.610...              12
13  MULTIPOINT (304591.429 4298959.914, 304591.683...              13
14  MULTIPOINT (304589.943 4298959.471, 304590.265...              14
15  MULTIPOINT (304592.258 4298960.104, 304592.462...              15
16  MULTIPOINT (304591.253 4298959.867, 304591.507...              16
17  MULTIPOINT (304591.918 4298960.033, 304592.122...              17
18  MULTIPOINT (304590.664 4298959.763, 304590.891...              18
19  MULTIPOINT (304591.465 4298959.938, 304591.670...              19
20  MULTIPOINT (304589.080 4298959.361, 304589.354...              20
21  MULTIPOINT (304590.472 4298959.718, 304590.699...              21
22  MULTIPOINT (304587.172 4298958.760, 304587.505...              22
23  MULTIPOINT (304588.905 4298959.311, 304589.178...              23
24  MULTIPOINT (304586.119 4298958.375, 304586.478...              24
25  MULTIPOINT (304586.967 4298958.688, 304587.301...              25

#### Method 3

In [16]:
import geopandas as gpd
from shapely.geometry import MultiPoint

# Assuming gdf_line is your GeoDataFrame with LineString geometries

# Initialize an empty list to store GeoDataFrames for each line
gdfs_per_line = []

for index, row in gdf_line.iterrows():
    line = row['geometry']  # Extract the LineString geometry from the current row

    distance = 0
    add_distance = 1
    list_of_points = []

    point_id = 1  # Initialize point ID

    while distance < line.length:
        new_point = line.interpolate(distance)
        list_of_points.append({'geometry': new_point, 'point_id': point_id})
        distance += add_distance
        point_id += 1  # Increment point ID

    # Create a GeoDataFrame for the current line
    gdf_line_points = gpd.GeoDataFrame(list_of_points, geometry='geometry')
    
    # Append the GeoDataFrame to the list
    gdfs_per_line.append(gdf_line_points)

# Now, gdfs_per_line is a list where each element is a GeoDataFrame containing points for a single line


In [17]:
gdfs_per_line

[                          geometry  point_id
 0   POINT (302435.909 4300263.369)         1
 1   POINT (302435.199 4300262.665)         2
 2   POINT (302434.489 4300261.961)         3
 3   POINT (302433.778 4300261.257)         4
 4   POINT (302433.068 4300260.553)         5
 5   POINT (302432.358 4300259.849)         6
 6   POINT (302431.648 4300259.145)         7
 7   POINT (302430.937 4300258.441)         8
 8   POINT (302430.227 4300257.737)         9
 9   POINT (302429.517 4300257.033)        10
 10  POINT (302428.807 4300256.329)        11
 11  POINT (302428.096 4300255.625)        12
 12  POINT (302427.386 4300254.921)        13
 13  POINT (302426.676 4300254.217)        14
 14  POINT (302425.966 4300253.513)        15
 15  POINT (302425.255 4300252.810)        16
 16  POINT (302424.545 4300252.106)        17
 17  POINT (302423.835 4300251.402)        18
 18  POINT (302423.124 4300250.698)        19
 19  POINT (302422.414 4300249.994)        20
 20  POINT (302421.704 4300249.290

#### sample

In [18]:
import rasterio
import geopandas as gpd
import numpy as np

# Assuming gdfs_per_line is a list containing GeoDataFrames

def extract_raster_values(point, src):
    values = list(src.sample([(point.x, point.y)]))

    # Return the sampled values as float
    return float(values[0][0]) if values and not np.isnan(values[0][0]) else np.nan

raster_path = r"C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\03-Shapefile\01-New_domain_data\02-DEM\02-Fairfax_County_2018\clip\clip_ffxco.tif"

for gdf_line_points in gdfs_per_line:
    src = rasterio.open(raster_path)
    gdf_line_points['raster_values'] = gdf_line_points['geometry'].apply(lambda geom: extract_raster_values(geom, src))
    src.close()
    
    # Optionally, round the raster_values column
    gdf_line_points['raster_values'] = gdf_line_points['raster_values'].round(4)


C:\Users\zkhalid5\AppData\Roaming\Python\Python311\site-packages\geopandas\geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)
C:\Users\zkhalid5\AppData\Roaming\Python\Python311\site-packages\geopandas\geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(func, convert_dtype=convert_dtype, args=args, **kwargs)
C:\Users\zkhalid5\AppData\Roaming\Python\Python311\site-packages\geopandas\geoseries.py:645: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  result = super().apply(

In [436]:
gdfs_per_line

[                          geometry  point_id  raster_values
 0   POINT (304581.180 4298952.716)         1        74.7549
 1   POINT (304580.266 4298952.309)         2        74.7592
 2   POINT (304579.353 4298951.903)         3        74.7952
 3   POINT (304578.439 4298951.496)         4        74.7895
 4   POINT (304577.526 4298951.089)         5        74.7587
 5   POINT (304576.612 4298950.682)         6        74.7844
 6   POINT (304575.699 4298950.276)         7        74.7772
 7   POINT (304574.785 4298949.869)         8        74.8416
 8   POINT (304573.872 4298949.462)         9        74.8457
 9   POINT (304572.958 4298949.056)        10        74.8324
 10  POINT (304572.044 4298948.649)        11        74.8721
 11  POINT (304571.131 4298948.242)        12        74.8632
 12  POINT (304570.217 4298947.835)        13        74.8835
 13  POINT (304569.304 4298947.429)        14        74.7395
 14  POINT (304568.390 4298947.022)        15        74.2926
 15  POINT (304567.477 4

#### Slope

In [23]:
gdfs_per_line_with_slope = [calculate_relative_slope(gdf_line) for gdf_line in gdfs_per_line]

In [27]:
gdfs_per_line_with_slope

[                          geometry  point_id  raster_values   slope
 0   POINT (302435.909 4300263.369)         1       100.4699     NaN
 1   POINT (302435.199 4300262.665)         2       100.5036 -1.2604
 2   POINT (302434.489 4300261.961)         3       100.5842 -1.3410
 3   POINT (302433.778 4300261.257)         4       100.6100 -1.3668
 4   POINT (302433.068 4300260.553)         5       100.6656 -1.4224
 5   POINT (302432.358 4300259.849)         6       100.6872 -1.4440
 6   POINT (302431.648 4300259.145)         7       100.6929 -1.4497
 7   POINT (302430.937 4300258.441)         8       100.7664 -1.5232
 8   POINT (302430.227 4300257.737)         9       100.7456 -1.5024
 9   POINT (302429.517 4300257.033)        10       100.8320 -1.5888
 10  POINT (302428.807 4300256.329)        11       100.7126 -1.4694
 11  POINT (302428.096 4300255.625)        12       100.6740 -1.4308
 12  POINT (302427.386 4300254.921)        13       100.6904 -1.4472
 13  POINT (302426.676 4300254.217

In [476]:


# Concatenate all GeoDataFrames into a single GeoDataFrame
merged_gdf = pd.concat(gdfs_per_line_with_slope, ignore_index=True)

# Convert the merged GeoDataFrame to a shapefile
shapefile_path = r'C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\first_transact_line12345678920.shp'
merged_gdf.to_file(shapefile_path, driver='ESRI Shapefile')


C:\Users\zkhalid5\AppData\Local\Temp\ipykernel_2292\3932935817.py:6: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  merged_gdf.to_file(shapefile_path, driver='ESRI Shapefile')


#### Filtering 

In [24]:
def prune_middle_to_bottom(df):
    middle_index = len(df) // 2

    for i, row in df.iloc[middle_index:].iterrows():
        current_id = row['point_id']
        
        if i < len(df) - 1:
            next_id = df.loc[i + 1, 'point_id']
            
            if abs(current_id - next_id) > 2:
                return df.iloc[:i + middle_index + 1]

    return df


In [25]:
# Apply the functions to each GeoDataFrame in gdfs_per_line_with_slope
filtered_gdfs = [filter_slope_range(gdf_line) for gdf_line in gdfs_per_line_with_slope]
pruned_gdfs = [prune_middle_to_bottom(prune_bottom_to_top(gdf_line)) for gdf_line in filtered_gdfs]

In [441]:
pruned_gdfs

[                          geometry  point_id  raster_values   slope
 0   POINT (304580.266 4298952.309)         2        74.7592 -0.8698
 1   POINT (304579.353 4298951.903)         3        74.7952 -0.9058
 2   POINT (304578.439 4298951.496)         4        74.7895 -0.9001
 3   POINT (304577.526 4298951.089)         5        74.7587 -0.8693
 4   POINT (304576.612 4298950.682)         6        74.7844 -0.8950
 5   POINT (304575.699 4298950.276)         7        74.7772 -0.8878
 6   POINT (304574.785 4298949.869)         8        74.8416 -0.9522
 7   POINT (304573.872 4298949.462)         9        74.8457 -0.9563
 8   POINT (304572.958 4298949.056)        10        74.8324 -0.9430
 9   POINT (304572.044 4298948.649)        11        74.8721 -0.9827
 10  POINT (304571.131 4298948.242)        12        74.8632 -0.9738
 11  POINT (304570.217 4298947.835)        13        74.8835 -0.9941
 12  POINT (304569.304 4298947.429)        14        74.7395 -0.8501
 13  POINT (304568.390 4298947.022

#### Banks only

In [ ]:
processing.run("qgis:knearestconcavehull", {'INPUT':'C:/01-Work-Data-Archieve/07-Active_Projects/01-Data/08-shape_output/first_transact_line12345678914.shp','KNEIGHBORS':15,'FIELD':'','OUTPUT':'TEMPORARY_OUTPUT'})

In [ ]:
processing.run("qgis:concavehull", {})

#### save to shapefile

In [26]:


# Concatenate all GeoDataFrames into a single GeoDataFrame
merged_gdf = pd.concat(pruned_gdfs, ignore_index=True)

# Convert the merged GeoDataFrame to a shapefile
shapefile_path = r'C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\first_transact_line12345678921.shp'
merged_gdf.to_file(shapefile_path, driver='ESRI Shapefile')


C:\Users\zkhalid5\AppData\Local\Temp\ipykernel_26916\3322107588.py:6: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  merged_gdf.to_file(shapefile_path, driver='ESRI Shapefile')


In [301]:
output_path = r'C:\01-Work-Data-Archieve\07-Active_Projects\01-Data\08-shape_output\first_transact_line12345678912.shp'
gdfs_per_line.to_file(output_path, driver='ESRI Shapefile')

AttributeError: 'list' object has no attribute 'to_file'